<a href="https://colab.research.google.com/github/ayakow1/ttic31220-japanparliament-analysis/blob/main/BERTopic.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **Tutorial** - Topic Modeling with BERTopic
(last updated 01-09-2022)

In this tutorial we will be exploring how to use BERTopic to create topics from the well-known 20Newsgroups dataset. The most frequent use-cases and methods are discussed together with important parameters to keep a look out for. 


## BERTopic
BERTopic is a topic modeling technique that leverages 🤗 transformers and a custom class-based TF-IDF to create dense clusters allowing for easily interpretable topics whilst keeping important words in the topic descriptions. 

<br>

<img src="https://raw.githubusercontent.com/MaartenGr/BERTopic/master/images/logo.png" width="40%">

# Enabling the GPU

First, you'll need to enable GPUs for the notebook:

- Navigate to Edit→Notebook Settings
- select GPU from the Hardware Accelerator drop-down

[Reference](https://colab.research.google.com/notebooks/gpu.ipynb)

# **Installing BERTopic**

We start by installing BERTopic from PyPi:

In [1]:
%%capture
!pip install bertopic

## Restart the Notebook
After installing BERTopic, some packages that were already loaded were updated and in order to correctly use them, we should now restart the notebook.

From the Menu:

Runtime → Restart Runtime

# Data
For this example, we use the popular 20 Newsgroups dataset which contains roughly 18000 newsgroups posts

In [1]:
from google.colab import drive
drive.mount("/content/drive")

Mounted at /content/drive


In [2]:
import sqlite3
import pandas as pd
from bertopic import BERTopic


In [3]:
conn = sqlite3.connect('/content/drive/MyDrive/議事録/raw_speech.db')

In [5]:
all = pd.read_sql_query(f'''SELECT * FROM raw_speech WHERE speech_date >= '2022-01-01' AND speech_date <= '2023-04-31' ''', conn)

In [6]:
docs = all['speech'].to_list()

In [7]:
conn.close()

# **Topic Modeling**

In this example, we will go through the main components of BERTopic and the steps necessary to create a strong topic model. 




## Training

We start by instantiating BERTopic. We set language to `english` since our documents are in the English language. If you would like to use a multi-lingual model, please use `language="multilingual"` instead. 

We will also calculate the topic probabilities. However, this can slow down BERTopic significantly at large amounts of data (>100_000 documents). It is advised to turn this off if you want to speed up the model. 


In [9]:
topic_model = BERTopic(language="multilingual", verbose=True, embedding_model="paraphrase-multilingual-mpnet-base-v2") #https://tech.yellowback.net/posts/sentence-transformers-japanese-models
topics, probs = topic_model.fit_transform(docs) # Input is list type
# https://github.com/UKPLab/sentence-transformers/issues/1915 multilingual はエラー

Batches:   0%|          | 0/1582 [00:00<?, ?it/s]

2023-05-09 20:14:09,808 - BERTopic - Transformed documents to Embeddings
2023-05-09 20:15:40,556 - BERTopic - Reduced dimensionality
2023-05-09 20:15:46,873 - BERTopic - Clustered reduced embeddings


**NOTE**: Use `language="multilingual"` to select a model that support 50+ languages.

## Extracting Topics
After fitting our model, we can start by looking at the results. Typically, we look at the most frequent topics first as they best represent the collection of documents. 

In [10]:
freq = topic_model.get_topic_info(); freq.head(5)

Topic  Count               Name
0     -1  24681    -1_という_です_ます_こと
1      0    888  0_感染_感染症_医療_オミクロン
2      1    683  1_課税_消費税_インボイス_税制
3      2    624   2_予算_予備費_補正予算_年度
4      3    614      3_病院_医療_医師_患者

-1 refers to all outliers and should typically be ignored. Next, let's take a look at a frequent topic that were generated:

In [11]:
topic_model.get_topic(0)  # Select the most frequent topic

[('感染', 0.009401529212894808),
 ('感染症', 0.007597229131315474),
 ('医療', 0.006006866313622901),
 ('オミクロン', 0.005368064391440536),
 ('新型コロナウイルス感染症', 0.005309756807647325),
 ('コロナ', 0.004837150527115102),
 ('感染拡大', 0.004814205663129526),
 ('ワクチン', 0.004782952591902243),
 ('医療機関', 0.004751992665339528),
 ('新型コロナ', 0.004458747409207438)]

**NOTE**: BERTopic is stocastich which mmeans that the topics might differ across runs. This is mostly due to the stocastisch nature of UMAP.

In [ ]:
### Attributes

## Attributes

There are a number of attributes that you can access after having trained your BERTopic model:


| Attribute | Description |
|------------------------|---------------------------------------------------------------------------------------------|
| topics_               | The topics that are generated for each document after training or updating the topic model. |
| probabilities_ | The probabilities that are generated for each document if HDBSCAN is used. |
| topic_sizes_           | The size of each topic                                                                      |
| topic_mapper_          | A class for tracking topics and their mappings anytime they are merged/reduced.             |
| topic_representations_ | The top *n* terms per topic and their respective c-TF-IDF values.                             |
| c_tf_idf_              | The topic-term matrix as calculated through c-TF-IDF.                                       |
| topic_labels_          | The default labels for each topic.                                                          |
| custom_labels_         | Custom labels for each topic as generated through `.set_topic_labels`.                                                               |
| topic_embeddings_      | The embeddings for each topic if `embedding_model` was used.                                                              |
| representative_docs_   | The representative documents for each topic if HDBSCAN is used.                                                |

For example, to access the predicted topics for the first 10 documents, we simply run the following:

In [12]:
topic_model.topics_[:10]

[173, 173, 108, -1, 1, -1, 26, 4, 82, -1]

# **Visualization**
There are several visualization options available in BERTopic, namely the visualization of topics, probabilities and topics over time. Topic modeling is, to a certain extent, quite subjective. Visualizations help understand the topics that were created. 

## Visualize Topics
After having trained our `BERTopic` model, we can iteratively go through perhaps a hundred topic to get a good 
understanding of the topics that were extract. However, that takes quite some time and lacks a global representation. 
Instead, we can visualize the topics that were generated in a way very similar to 
[LDAvis](https://github.com/cpsievert/LDAvis):

In [13]:
topic_model.visualize_topics()

## Visualize Topic Probabilities

The variable `probabilities` that is returned from `transform()` or `fit_transform()` can 
be used to understand how confident BERTopic is that certain topics can be found in a document. 

To visualize the distributions, we simply call:

In [14]:
topic_model.visualize_distribution(probs[200], min_probability=0.015)

ValueError: ignored

## Visualize Topic Hierarchy

The topics that were created can be hierarchically reduced. In order to understand the potential hierarchical structure of the topics, we can use scipy.cluster.hierarchy to create clusters and visualize how they relate to one another. This might help selecting an appropriate nr_topics when reducing the number of topics that you have created.

In [15]:
topic_model.visualize_hierarchy(top_n_topics=50)

## Visualize Terms

We can visualize the selected terms for a few topics by creating bar charts out of the c-TF-IDF scores for each topic representation. Insights can be gained from the relative c-TF-IDF scores between and within topics. Moreover, you can easily compare topic representations to each other.

In [16]:
topic_model.visualize_barchart(top_n_topics=5)

## Visualize Topic Similarity
Having generated topic embeddings, through both c-TF-IDF and embeddings, we can create a similarity matrix by simply applying cosine similarities through those topic embeddings. The result will be a matrix indicating how similar certain topics are to each other.

In [17]:
topic_model.visualize_heatmap(n_clusters=20, width=1000, height=1000)

## Visualize Term Score Decline
Topics are represented by a number of words starting with the best representative word. Each word is represented by a c-TF-IDF score. The higher the score, the more representative a word to the topic is. Since the topic words are sorted by their c-TF-IDF score, the scores slowly decline with each word that is added. At some point adding words to the topic representation only marginally increases the total c-TF-IDF score and would not be beneficial for its representation.

To visualize this effect, we can plot the c-TF-IDF scores for each topic by the term rank of each word. In other words, the position of the words (term rank), where the words with the highest c-TF-IDF score will have a rank of 1, will be put on the x-axis. Whereas the y-axis will be populated by the c-TF-IDF scores. The result is a visualization that shows you the decline of c-TF-IDF score when adding words to the topic representation. It allows you, using the elbow method, the select the best number of words in a topic.


In [18]:
topic_model.visualize_term_rank()

# **Topic Representation**
After having created the topic model, you might not be satisfied with some of the parameters you have chosen. Fortunately, BERTopic allows you to update the topics after they have been created. 

This allows for fine-tuning the model to your specifications and wishes. 

## Update Topics
When you have trained a model and viewed the topics and the words that represent them,
you might not be satisfied with the representation. Perhaps you forgot to remove
stopwords or you want to try out a different `n_gram_range`. We can use the function `update_topics` to update 
the topic representation with new parameters for `c-TF-IDF`: 


In [19]:
topic_model.update_topics(docs, n_gram_range=(1, 2))

In [20]:
topic_model.get_topic(0)   # We select topic that we viewed before

[('感染', 0.006022871975610156),
 ('感染症', 0.0047626450845571254),
 ('医療', 0.004035820702679772),
 ('オミクロン', 0.0033092546352667587),
 ('コロナ', 0.003292358980643377),
 ('新型コロナウイルス感染症', 0.0032281790009872405),
 ('ワクチン', 0.0032186322929826593),
 ('医療機関', 0.002999386450187526),
 ('対策', 0.0029922750469425614),
 ('感染拡大', 0.002892182007115562)]

## Topic Reduction
We can also reduce the number of topics after having trained a BERTopic model. The advantage of doing so, 
is that you can decide the number of topics after knowing how many are actually created. It is difficult to 
predict before training your model how many topics that are in your documents and how many will be extracted. 
Instead, we can decide afterwards how many topics seems realistic:





In [21]:
topic_model.reduce_topics(docs, nr_topics=60)

2023-05-09 20:20:26,163 - BERTopic - Reduced number of topics from 411 to 60


In [22]:
# Access the newly updated topics with:
print(topic_model.topics_)

[16, 16, 16, -1, 8, -1, 11, 10, 34, -1, 14, 14, 14, 1, 16, 0, 16, -1, 0, -1, 13, -1, 2, 2, 2, 0, 10, -1, -1, -1, 10, -1, -1, -1, 10, -1, -1, -1, 0, -1, 2, -1, 0, -1, 3, 0, -1, -1, 1, -1, 25, 25, -1, 0, 16, 1, 5, 5, 5, 5, -1, -1, 9, 9, -1, -1, -1, 1, -1, 16, -1, 1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, 1, -1, -1, 3, -1, 34, 1, 16, 2, 2, -1, 2, 0, 23, 0, 1, 16, 7, -1, -1, 7, 7, 7, -1, 22, 16, 1, -1, 16, -1, 2, -1, 10, -1, 1, 10, 10, -1, 10, -1, 0, -1, 0, 6, 5, 1, -1, -1, -1, 6, -1, -1, -1, 1, 1, 1, -1, 43, 17, 3, 17, 2, -1, 10, 10, 1, -1, 1, -1, 2, 2, -1, -1, 2, 1, -1, 1, 1, 1, 2, -1, -1, 0, -1, -1, 1, 0, -1, -1, -1, -1, -1, -1, 1, 2, -1, 0, -1, -1, -1, -1, 0, -1, 0, -1, -1, 0, 0, 0, -1, -1, 1, 0, -1, 0, 0, 6, -1, 6, -1, 16, -1, -1, -1, -1, -1, -1, -1, 11, -1, -1, -1, 0, 0, 0, 0, 0, -1, -1, -1, 1, -1, -1, 0, -1, -1, 1, 10, -1, 38, -1, -1, -1, 1, -1, 0, 6, 0, 0, 1, -1, 7, 7, 0, 2, 2, 2, 2, 23, 0, 1, 30, 6, 0, 5, 0, -1, 0, 0, 0, 0, -1, -1, -1, 14, 2, -1, 2, 14, -1, 15, 5, -1, 34, 1, 

# **Search Topics**
After having trained our model, we can use `find_topics` to search for topics that are similar 
to an input search_term. Here, we are going to be searching for topics that closely relate the 
search term "vehicle". Then, we extract the most similar topic and check the results: 

In [25]:
similar_topics, similarity = topic_model.find_topics("感染症", top_n=5); similar_topics

[10, 54, 18, 26, 52]

In [27]:
topic_model.get_topic(10)

[('ワクチン', 0.045174056290862255),
 ('接種', 0.039832671231347656),
 ('ワクチン 接種', 0.017997855926165405),
 ('ます', 0.01177946901340277),
 ('です', 0.011056796801639648),
 ('という', 0.010541975053151137),
 ('ない', 0.010229847042357028),
 ('こと', 0.009804863825098828),
 ('から', 0.009324802972235249),
 ('これ', 0.009252808791673754)]

# **Model serialization**
The model and its internal settings can easily be saved. Note that the documents and embeddings will not be saved. However, UMAP and HDBSCAN will be saved. 

In [30]:
# Save model
topic_model.save("/content/drive/MyDrive/議事録/model")	

In [32]:
# Load model
my_model = BERTopic.load("/content/drive/MyDrive/議事録/model")	

# **Embedding Models**
The parameter `embedding_model` takes in a string pointing to a sentence-transformers model, a SentenceTransformer, or a Flair DocumentEmbedding model.

## Sentence-Transformers
You can select any model from sentence-transformers here and pass it through BERTopic with embedding_model:



In [ ]:
topic_model = BERTopic(embedding_model="xlm-r-bert-base-nli-stsb-mean-tokens")

Or select a SentenceTransformer model with your own parameters:


In [ ]:
from sentence_transformers import SentenceTransformer

sentence_model = SentenceTransformer("distilbert-base-nli-mean-tokens", device="cpu")
topic_model = BERTopic(embedding_model=sentence_model, verbose=True)

Click [here](https://www.sbert.net/docs/pretrained_models.html) for a list of supported sentence transformers models.  
